### selenium 패키지 설치 필요
### !pip install selenium 

In [6]:
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException
import numpy as np
import pandas as pd
import time
import json
import openpyxl
import re
import datetime
from tqdm import tqdm

### chromedriver.exe 설치 후 불러오기
### 버전에 맞게 설치
### 버전 확인 방법 : https://luminitworld.tistory.com/90?category=977373   참조

# 네이버 크롤러 클래스

In [7]:
class NaverCrawler():
    
    def __init__(self, driver):
        self.driver = driver
        #self.category_num = category  # 흠 보류
        
    def getOnePageUrls(self, url, headlineUrls):
        self.driver.get(url)
        time.sleep(1) # 이부분이 중요함 위의 url 접근 후 다음과 같이 시간을 줘야함 안주면 바로 넘어가서 오류 나옴
        url1=self.driver.find_elements_by_css_selector('div.section_body')
        dt_all=url1[0].find_elements_by_css_selector('dt')
        dt_title=dt_all

        for i in range(0, len(dt_title)):
            result=dt_title[i].find_elements_by_css_selector('a')[0].get_attribute("href")
            headlineUrls.append(result)  # 여기서는 headlineUrls 주소가 적용되는것 같음
    
        headlineUrls=list(dict.fromkeys(headlineUrls))
        #print('done')
        return headlineUrls
    
    def getLastPageNum(self, category_num):
        headlineUrls=list()
        driver2 = webdriver.Chrome('./chromedriver.exe')
        driver2.get(f'https://news.naver.com/main/main.nhn?mode=LSD&mid=shm&sid1=10{category_num}#&date=%2000:00:00&page=5000')
        last_page = driver2.find_elements_by_css_selector('div.paging>strong')
        last_page = last_page[0].text
        #print('마지막페이지 : ',last_page)
        last_page = int(last_page)
        return last_page
        
    def getUrls(self, category_num, PATH):
        
        headlineUrls = list()
        last_page = self.getLastPageNum(category_num)
        print('마지막 페이지: ',last_page)
        for k in tqdm(range(1,last_page+1)):
            #print(f'{category_num} category page:',k)
            headlineUrls=self.getOnePageUrls(f'https://news.naver.com/main/main.nhn?mode=LSD&mid=shm&sid1=10{category_num}#&date=%2000:00:00&page={k}', headlineUrls)
            #print('done for문 ',k)
            time.sleep(0.3)
        df = pd.DataFrame(headlineUrls)
        df.to_csv(PATH+f'/naver_{category_num}_urls.csv', index=None)
        
        # 이 다음에 자신이 설정한 filepath에 해당 headlineUrls를 csv로 저장하도록 하기
        # 위 처럼 하면 이 밑의 return은 없앨것임 ㅇㅇ
        #return headlineUrls
    
    def get_article(self, urls, PATH):  # num 은 text파일명의 순번 부분
        data = {}
        
        now = datetime.datetime.now()
        nowDate = now.strftime('%Y-%m-%d')
    
        for i in tqdm(range(0,len(urls))):
            url=urls[i]
            self.driver.get(url)
            time.sleep(0.3)
            
            title = self.driver.find_elements_by_css_selector('h3#articleTitle')
            if(len(title)==0):
                continue
            
            title = title[0].text    # 제목
        
            date = self.driver.find_elements_by_css_selector('span.t11')
            date = date[0].text[0:10]
            date = date.replace(".","-")  # 날짜
            if(i==0):
                start_date = date
            end_date = date


            url3 = self.driver.find_elements_by_css_selector('div._article_body_contents')
            raw_article=url3[0].text   # 내용
        
            category = self.driver.find_elements_by_css_selector('em.guide_categorization_item')[0].text # 범주
        
            if(len(self.driver.find_elements_by_css_selector('em.img_desc'))!=0):  # 만약에 이미지가 기사에 존재한다면 그 부분 없애기 
                img_text = self.driver.find_elements_by_css_selector('em.img_desc')[0].text
                raw_article = raw_article.replace(img_text,'')
        
            if(len(self.driver.find_elements_by_css_selector('strong.media_end_summary'))!=0):      
                summary = self.driver.find_elements_by_css_selector('strong.media_end_summary')[0].text
                raw_article = raw_article.replace(summary,'')
        
            news_type = 'article'  # 뉴스 타입
        
            if(raw_article.find('동영상 뉴스')==0): # 동영상 뉴스일 경우
                news_type = 'video'  # 뉴스 타입
                raw_article = raw_article.replace('동영상 뉴스\n','')
            
            data_info = {
                "date" : date,
                "url" : url,
                "news_type" : news_type,
                "category" : category,
                "content" : raw_article
            
            }
            data[title]= data_info
            #time.sleep(0.3)
        
        with open(PATH+f'/naver_content_{category}({start_date}~{end_date}).json', 'w') as outfile:
            json.dump(data, outfile, indent=4)
        
    
    def get_comments(self, url,category_num, PATH):  # whoareU를 category_num으로 이따 바꾸기
        comments=list()
        self.driver.implicitly_wait(5)
    
        for i in tqdm(range(0,len(url))):
            while(True):
                try:
                    totalNum=0
                    self.driver.get(url[i])
                    elem=self.driver.find_elements_by_xpath('//*[@id="articleTitleCommentCount"]')  
                    time.sleep(0.5)  # 이거해야함
                    if(len(elem)==0):
                        break
                    
                    elem_c_num = elem[0].find_elements_by_css_selector('span.lo_txt')
                    time.sleep(0.5)
                    if(len(elem_c_num[0].text)==0):  # 이거는 commentTitleCount가 없는경우에 에러뜨는거 방지용
                        break
                    
                    elem[0].click()
                    commentNum=self.driver.find_elements_by_css_selector('span.u_cbox_info_txt')
                    for j in range (0,len(commentNum)):
                        totalNum=totalNum+int(commentNum[j].text.replace(",",""))
                    
                    if totalNum > 2000:
                        totalNum = 200

                    if totalNum == 0:
                        break
                    elif totalNum%20 == 0:
                        moreClickNum = int(totalNum/20)-1
                    else:
                        moreClickNum = int(totalNum/20)

                    time.sleep(0.4)

                    if(len(self.driver.find_elements_by_xpath('//*[@id="cbox_module"]/div[2]/div[9]/a'))==0):
                        more_click = self.driver.find_elements_by_xpath('//*[@id="cbox_module"]/div/div[9]/a')[0]
                    else:
                        more_click = self.driver.find_elements_by_xpath('//*[@id="cbox_module"]/div[2]/div[9]/a')[0]
                    for m in range (0,moreClickNum):
                        more_click.click() # 이게 더보기 눌러주는것
                        time.sleep(0.1)

                    comment = self.driver.find_elements_by_css_selector('div.u_cbox_text_wrap') # 해당 공통된 놈 다 가져오는 꼴임
                    for k in range (0,len(comment)):
                        if comment[k].text == '작성자에 의해 삭제된 댓글입니다.' or comment[k].text == '클린봇이 부적절한 표현을 감지한 댓글입니다.':
                            continue
                        #print(comment[k].text)
                        comments.append(comment[k].text)
                    #print('task: ',i)
                    break
                    
                #except UnexpectedAlertPresentException:
                #    alertblock = self.driver.switch_to_alert()
                #    alertblock.accept()
                #    time.sleep(5)
                
                except TimeoutException:
                    break
                
                except:
                    print(self.driver.current_url)
                    break
                
        if(len(comments)!=0):
            df = pd.DataFrame(comments)
            now = datetime.datetime.now()
            nowDate = now.strftime('%Y-%m-%d %H-%M')  # 파일명용
        
            if(category_num==0):
                df.to_excel(PATH+f'/naver_gov_comments({nowDate}).xlsx', header =['comment'], index=None)
            elif(category_num==1):
                df.to_excel(PATH+f'/naver_econ_comments({nowDate}).xlsx', header =['comment'], index=None)
            elif(category_num==2):
                df.to_excel(PATH+f'/naver_soc_comments({nowDate}).xlsx', header =['comment'], index=None)
            elif(category_num==3):
                df.to_excel(PATH+f'/naver_life_comments({nowDate}).xlsx', header =['comment'], index=None)
            elif(category_num==4):
                df.to_excel(PATH+f'/naver_world_comments({nowDate}).xlsx', header =['comment'], index=None)
            elif(category_num==5):
                df.to_excel(PATH+f'/naver_it_comments({nowDate}).xlsx', header =['comment'], index=None)
        else:
            print('추출한 기사에 댓글이 하나도 없습니다.')
        
        print('category num :',category_num)
        print('추출한 댓글 수 :',len(comments))

# 실행코드

### 저장할 경로 설정

In [8]:
PATH_URL_LIST = './new'
PATH_CONTENTS = './new/naver_contents'
PATH_COMMENTS = './new/naver_comments'
ONE_EXCEL_NUM = 500  # comment 수집 시 한 엑셀 파일에 몇 개 기사의 댓글들을 넣을 지 설정

PATH_URL_LIST  :  카테고리마다의 URL list들이 저장된 exce파일 위치 설정  
PATH_CONTENTS  :  기사 내용 json파일 저장 될 디렉터리 위치 설정  
PATH_COMMENTS  :  기사 댓글 xlsx파일 저장 될 디렉터리 위치 설정  

## category_num
### 0 : 정치,  1 : 경제,  2 : 사회,  3 : 생활,  4 : 세계,  5 : IT/과학

categroy_list의 원소에 추출할 category_num의 번호들을 넣어주면 해당 번호에 맞는 카테고리에 대한 결과물들을 크롤링함   
category_list = [0, 1, 2, 3, 4, 5]   ->   6개 카테고리 모두 수행함

In [9]:
driver = webdriver.Chrome('./chromedriver.exe')
a = NaverCrawler(driver)

WebDriverException: Message: 'chromedriver.exe' executable needs to be in PATH. Please see https://sites.google.com/a/chromium.org/chromedriver/home


2와 3의 기능을 실행하기 전에 반드시 1의 기능이 완료되어야 실행 가능(category list에 설정한 카테고리들만 가능)

# 1. 카테고리별 list 저장

In [1]:
category_list = [0,1,2,3,4,5]      # category_list 원소 설정하기
for i in category_list:
    a.getUrls(i,PATH_URL_LIST)

NameError: name 'a' is not defined

# 2. 카테고리 기사 내용 추출 

In [231]:
category_list = [0]
for i in category_list:
    df = pd.read_csv(PATH_URL_LIST+f'/naver_{i}_urls.csv')
    urls_list = df['0'].tolist()
    a.get_article(urls_list, PATH_CONTENTS)

100%|██████████████████████████████████████████████████████████████████████████████| 1546/1546 [29:35<00:00,  1.15s/it]


In [235]:
with open(PATH_CONTENTS+f'/naver_content_IT(2021-08-30~2021-08-23).json', 'r') as json_file:
    json_data = json.load(json_file)

In [241]:
json_data

{'[노재웅의 가치 스타트UP]AI로 공간활용 신의 한 수 ‘파이미디어랩’': {'date': '2021-08-30',
  'url': 'https://news.naver.com/main/read.naver?mode=LSD&mid=shm&sid1=105&oid=018&aid=0005023138',
  'news_type': 'article',
  'category': 'IT',
  'content': '\n여병상(오른쪽) 파이미디어랩 대표와 김현진 선임연구원이 ‘디지코KT 오픈랩’에 적용한 스마트 좌석제 키오스크 앞에서 자세를 취하고 있다. KT 제공\n\n가치 있는 스타트업을 올립(UP)니다. 노재웅 기자가 스타트업과 같이(가치) 합니다. 이곳에서 함께 기업과 자신의 가치를 올리실 분 계신가요?\n[이데일리 노재웅 기자] KT(030200)가 지난 7월 스타트업 육성의 메카로 만들겠다며 서울 관악구에 세운 ‘디지코KT 오픈랩’. 오픈랩 설립 소식을 듣자마자 대표기업 인터뷰를 요청했고, 7개 입주기업 중 가장 먼저 KT가 소개한 회사는 법인 설립 2개월 만에 KT의 픽을 받는 데 성공한 유망 인공지능(AI) 스타트업 ‘파이미디어랩’이었다.\n\n“비전공자도 AI 전문가 만들어줘요”\n\n디지코KT 오픈랩에는 공유오피스로 들어서는 초입에 스마트 좌석제 이용을 위한 키오스크가 있다. 내가 일할 좌석이나 휴게실, 락커를 실시간으로 예약하고 들어가는 방식인데, 키오스크를 손으로 직접 터치하지 않아도 인공지능(AI) 카메라가 사용자의 손동작을 인식해 원격으로 화면을 제어할 수 있다.\n\n예약을 마치면 내 자리에는 명함꽂이만한 디스플레이에 자동으로 회사명과 이름이 표기된다. 이를 통해 쓸데없는 조명이나 냉난방 시설의 낭비도 없애고, 업무 규모에 따라 장소도 효율적으로 쓸 수 있다.\n\n센터는 KT가 세웠지만, 이 시스템은 KT가 만든 것이 아니라고 한다. 회사 설립 2개월 만에 KT의 선택을 받아 디지코KT 오픈랩에 입성한 AI 공간 디지털전환(DX) 스타트업 파이미

# 3. 카테고리 기사 댓글 추출

In [260]:
category_list = [5]
for i in category_list:
    df = pd.read_csv(PATH_URL_LIST+f'/naver_{i}_urls.csv')
    urls_list = df['0'].tolist()
    
    start_idx = 0
    end_idx = start_idx + ONE_EXCEL_NUM
    
    if(len(urls_list) % ONE_EXCEL_NUM==0):
        num = int(len(urls_list) / ONE_EXCEL_NUM)-1
    else:
        num = int(len(urls_list) / ONE_EXCEL_NUM)
    for j in range(0, num):
        a.get_comments(urls_list[start_idx:end_idx],i, PATH_COMMENTS)
        start_idx = start_idx+ ONE_EXCEL_NUM
        end_idx = end_idx + ONE_EXCEL_NUM

삼성 이재용을 가옥에ㅣ 가둬 둔것이 중국을 위한 정치가 아니었을까 하는 합리적 의심이 드네 ᆢ
5G요금이 부담 기냥lte쓸란다
5g요금이 가치가있으려면 아직3년은더지나봐야함아직수도권일부외 벗어나면 lte 지방은 더하고..아직 5g요금제는 호구용임
점유율 지키겠다고 저가폰 외주주고 로고만 붙여 팔던데 제발 급떨어지는 짓좀 그만하자.. 팔다리 다 잘린 갤럭시 쥐어줘봤자 그런 구매자들은 사용자경험만 안좋고 결국 다 이탈한다고..
그가격으로 중저가 폰 내놓음 이길수 있겠나?
ㅋㅋㅋ 저기 중국산 ODM에 삼성 로고만 찍은 게 있을까 없을까? ㅋㅋㅋㅋㅋㅋㅋ
쓸데없이 부피커지는 접는 폰 만드니까 그렇지
task:  1
질병청 브리핑 할줄 아는거 : 앵무새마냥 2주연장 반복하기^^
ㅋㅋㅋㅋ 정부놈들 지들이 애초애 방역조치 제대로했으면 이사단까지 안났지 ㅋㅋㅋ 지들은 그냥 카메라 앞에서만 힘든척하고 국민분들에게 말로만 지시내리고 방역 지키라하고 지들은 카메라없으면 앉아서 그냥 아무것도안하고 ㅋㅋㅋ 참 웃음밖에 안나오네 ㅋㅋ
🐕똥같이 풀고 조이고 하지말고 확실히 좋아지면 풀어라 애들 장난도 아니고 이랬다 저랬다 짜증난다
자영업자 그만 ^^ 괴롭혀 자영업자는 당장 뒤지더라도 할사람 많으니 방역 희생자로 삼았냐? 아니 코로나가 야행성이냐? 낮에 2명 제한해라 개 불편해 뒤지긋다 퇴근하면 먹을대가 없어
24시간 통행금지 3일만 시켜바라 한자릿수간다 꼭필요한 공공기관이나업체 소수만출근시키고해바라 이게머냐 경제적으로 어마무시한 타격만주구장창 주고잇으니 ㅉㅉ
러시아산 백신을 도입해서 확산세를 꺾기나 해라
자영업자 목조이는방역이제 그만좀하세요
task:  2
AI 뇌출혈 진단 의료기기가 상용화되어 신속하게 환자의 뇌 CT 영상을 분석하고, 의료진이 골든 타임을 놓치지 않고 빠르게 뇌출혈에 대응할 미래가 기대됩니다. 의료진이 놓칠 수도 있는 미세한 출혈까지 판독할 수 있다니 정말 훌륭한 기술인 것 같습니다. 또한 전문의가 부족한 곳에 이 기술을 도입한다면 의료 격차 해소에도 큰 도움이 될 것

증여세 아낄라고 ㅎㅎㅎ 코인으로 불리면 되지 ~
리니지 사행성도좀 보자
Y
알바 햇겟지 ㅎㅎㅎ
미래에 뉴욕 월가에서 일할 트레이더들이다.. 지금부터라도 잘 받들어 모셔라~
그냥 냅두자잃어도 본인탓 따도 본인탓
보나마나 일진들이 반학우들한테 삥뜯어서 코인했겠지 ㅋㅋㅋ 부자가 아니고서는 ㅋㅋㅋㅋ
그러니까 애초에 미성년자 입금규제 자체가 없없다는거자나 ㅋㅋㅋㅋㅋㅋ 어른이 바른길로 인도한다더만 시세나 떨궈놨지 조치라고는 1그램도 안햌ㅋㅋㅋㅋㅋㅋㅋㅋ
틀레반들 탈세할려고 쇼하는거지
문재앙정부놈들 이제 애들 코묻은 돈도 탐내는거냐?
진짜 돈 주고 가짜 돈 사는 웃기는 세상.
10대20대 니네들이 마지막 종점인거 같다 ㅋㅋ 한심한
이제 코인은 진짜 끝이지 예전의 그 말도 안되는 수익을 보게 될 일은 없다
다들 얼릉 코인 탈출해라ㅋㅋㅋ대한민국 대표 징크스로 중고등학생들이 많이 시작하면 뭐든 다 망한다
사라진다!!!
10대는 부자되면 안되니? 노인세대들은 돈이 많아야하고, 10대는 돈이 많으면 이상하다고 생각하는게 이유가 뭐지??
캬 이제 10 대한테도 사행성 도박이 ㅋㅋㅋ실물 실체가 없는건 자산이 아님 ㅋㅋ
100만원에서 10프로 올라가면 110만원지만. 110에서 10프로 내려가면 99만이여. 확률적으로 돈을 잃은다는거지 100명중 한명만 코인으로 돈벌어. 투자를 할꺼면 20대에 총알 모아서 기회를 잘봐서 30대에 투자해
task:  9
누구?
잇섭채널 재밋어요 ㅋㅋ 진심으로 까는분들보면 신기한게 집에서 홈쇼핑 방송보면서도 진심모드 되서 집중하심??? ㅋㅋㅋㅋ
근데이기사가그렇게중요한가?뭐다이얘기야ㅋ플립3받아서잘쓰고있는데 뉴스거리참없나보네
에휴 또 엽츙이들 달려드는거봐라; 소비자입장에서 솔직한 리뷰한게 뭐가 죄라고; 요즘따라 엽츙이가 더 극성이네 신제품 출시라그란가
미친 언제적 기사를 아직도 재업하는 기자가있네 임 몇주전에 나온기사를 그것도 따른기자가이미 쓴걸 다시 배기는수준의기사 그리기사거리가없냐
kt인터넷 터뜨린걸로 일반인한테까지 유명해지니까 기자들이 날로 처먹으려고 렉카

이런 회사가 망해야 한국게임의 질이 올라가지
이제는 사업모델 바꿀 때도 되지 않았나...? 리니지가 캐시카우인건 알겠는데, 캐시카우는 잘 운영하면서 계속 새로운 걸 도전해야지. 이번에 나온 도깨비가 정말 인상 깊었던 것은 주타겟층을 '온 가족'으로 삼았다는 거임. 발상의 전환인거지... 청소년층이나 돈 많은 직장인들, 또는 백수들이 대상이 아니라 온 가족이 함께 할 수 있다는 게 얼마나 따뜻한 얘기냐? 리니지로 배 불렸으면 그걸 바탕으로 계속 혁신해라. IT잖아? 벤쳐정신이 기본으로 깔리는 거 아니었어? 왜 우물 안 개구리로 전락하려고 해? NC정신이 그런 거였어?
NC = Nimi Cival
아직까지 그딴 겜을 게임이라고 돈을 쓴 당신들이 한국 게임산업을 죽인 공범이다
돈을 써야 이기는 게임만드는 업체들 모조리 망해야 합니다
리니지가 흥한이유는 생각해보면 되게 간단함. 모든게 아데나라는 게임머니로 모든 장비를 살수 있었음. 그 아데나는 사냥하면 누구든 벌수 있었고. 지갑여유가 되는사람들은 그 아데나를 사서 고인첸 장비를 살수 있었고. 근데 지금은?? 시장경제가 게임하는 유저들한테 있는게 아니고 엔씨가 모든걸 통제하고 모든유저가 현질안하면 게임이 안되잖아.
유저들을 지갑으로만 보고 운영하니까 넷 게임들은 손대고 싶지 않다. 그래서 패키지 게임을 주로 하는데 이것들도 DLC 를 남발하니까 참 문제다.
아니 호구들이 각성했네..깨달을 때도 됬지, 바보도 아니고 콘솔이나 스팀게임에 맞들려 봐야 아!! 내가 지금 껏 하던건 게임이 아니라 쓰레기였구나 하고 느끼지
이젠 이런 회사는 없어져야 합니다.
민주당이 손 닿는 곳들은 어떻게 다 하나같이 저 따위로 결말을 맺냐 요새 트렌드인가
엔씨는. 때려잡아야될 기업이에요 사과 반성 속지마세요 ㅋㅋㅋㅋㅋ고객 무시. 악덕기업 중 이런 악덕기업. 없어요 후세를 주변지인들을 위해서라도 퇴출이 답이에요
택진이 형~! 이 답답한 사람아... 게임을 좀 1인칭 슈팅 게임도 개발하고 피파같은 축구 게임도 잘 좀 개발해봐라.... 무슨~ 리니

초심을잃은자 망하리라너무거만하다 미쳤어
변동확률제 불법사이버 도박수준의 BM을 가진 pay to win 겜 스레기들 다 망해야 게임산업이 부흥한다
엔간해야지.. ㅉ.
사회악
공교롭게도 펄 어비스 도깨비가 혹평하는데 한몫 했음
바다이야기 보다 악질적인 도박업체가 NC임컴플리트가챠 이런게 너무 당연하게 존재한다이런 양심없는 도박업체는 하루빨리 망해야함
엔씨는 한번도 경험하지 못 한 게임을 너무너무 잘 만든다! 특히 호구 주머니 털어먹는 아이템 게임ㅎㅎㅎ
기본현질은기본 운좋아야 템뜨고 할만하려면 월천만원 써야하고 노가다해봤자의미없고 옛날이좋았다
더 큰 문제는 그 페이 투 윈조차 정상적으로 일정액을 과금하면 확정적으로 p2w할 수 있는것도 아니고 '도박'이라는 점입니다. 돈을 지불하면 그에 상응하는 상품을 주는게 아닌 도박이 되니 해당 아이템을 얻기 위해 정상적 범주를 훨씬 상회하는 금액을 소수의 헤비유저들로부터 갈취하다시피 했고 우리나라 게임회사들이 그 기형적 매출로 매출액만 크게 늘려 거대기업들이 되었으니 우리나라에선 게임의 문화적 성장은 없고 모바일 강원랜드로 변질된겁니다.
엔씨는 못된짓만하는데 많은 사람들이 하는게 이해가 안갔었는데 이제 문닫을날만 남았네요ㅋㅋ프리서버도 아니고 아이템부터 모든걸 돈으로만 파는겜한다는게 이해가 갑니까?ㅋㅋㅋ
게임에 돈쓰는게 제일 아깝다.무기산다고,게임회사만 배불리는짓이지.
게임 아이템 구입으로 수백,수천,수억을 지불하는 유저가 겜 회사와 국가를 먹여 살렸다. 그 돈으로 주식 투자 했으면 수천,수억,수십억 되었을 것이다.
직원들 판매금액 대비 인센있나보죠...눈에 불켜고 돈벌어들이려고...이해가 가네...근데 적당히 좀...
이러나 저러나 택진이는 많이 묵었다
나는 이 쌍게임 접은지 오래 됐지 유저를 호구로아는 쌍NC 아이온때까지만 해도 참 좋았는데 "개구리 올챙이 적 생각 못한다"속담이 떠오르지
시대가 어느 때인데 시류를 읽지 못하고 페이 투 윈 게임, 것도 모자라 자가복제품을 줄줄이 찍어내냐. 정신 차리자. 에휴... 한숨이 나

엔씨의 공식 인증 개돼지인 린저씨가 시위할 정도면 끝장난거 아니냐?
참 요즘 유저들은 합리적인것 같아... 호구짓은 안해..
외국놈들 보유량이많은 주식인데 개미들은 손털어라
박석민 연봉 주려니~~
차라리 월정액을 해라.
바보들 이제그걸아냐...돈쓰고 영웅되면 뭐하냐...몇몇게이머들 돈버는거보고따라하냐...수천명이 그것도어린학생들 골병든다
아직도 리닌지를 하나
드뎌 정신들 차리는건가ㅋㅋ게임은 취미로 해야지.
게임중독자들은 정신병자 그이상임
첨부터 캐시템으로 겜하는게 문제지 누굴탓하냐
무료게임만 해도 할게 많은데... 한마디로 호구되는..
택진이 망햇네
진작에 이렇게 됐어야했지. 아직 늦지 않았다. 썩어빠진 한국 게임계를 바꿔보자
그냥 예전 처럼 월정액만 쳐받아라 아이텀현거래 가능하게 하고 폐인들은 그걸 원하고 있는것들이나호객들이주고객이 될것이다.
클래식 철회도 넣어라
엔씨게임이든 어떤게임이든 다 비슷하지ㅋㅋRPG가 돈쓴 만큼 강해지는거 아니냐?
도둑들
현질 좋다고하던 개돼지들이 드디어 정신차렸노?
나뻣어~힝!
이제 정신이 드냐?
게임개발사는 물론 개발자도 이제 유저들 눈치좀 봐야지... 니들의 고수익과 고연봉 다 어디서 나오는건데? 그럼 유저들도 수익 창출하게 해주던지 저비용으로 게임하게 해주던지. 뭔가 니들 게임을 하면서 이득을 보는게 있어야지. 재미? 재미있는다른게 널렸는데 왜 굳이 그걸 수억씩 지불하고 해야하니?
돈 써야 이기는 게임 밀고 돈 써야 진행되는 게임을 만들어. 아이템은 기본으로 쎈 거 주고 좋은 아이템 많이 나오는 던전에 유료 입장권을 만들어.
카지노인지도 모르고 카지노를 다니던 사람들이 이제서야 자신이 도박을 하고 있었음을 깨닫는다.
내 이럴줄ㅇ ㅏㄹ았지~~~~
고객돈 돈으로 잔치하나~
개발자 인건비 너무 높다
바보들아 열심히 월급 받아서 아이템 사라고 모지리들아
개뿔 떠나긴 ... 아직도 겁나 많이 하더만
김택진 돈독올랐지...
우리나라 기업이라는게 쪽팔린 지경에 이르렀다. 제발 망했으면
2.30대 지갑 터는 넘들ㅇ이 게임업체다.내가 좋아서

...

우웁
인간의 욕심이 끝을 모른다.....ㅠㅠ
좋은 기술이라는거에 동의는 하는데아직은 먹기에 썩 내키지는 않는다
배고프다 빨리 출시해라
쩐다.....
위 사진 젓소네 결국 육우 네ㅋ
항생제 잔뜩 쓰는 진짜고기 보다 더 건강에 좋을 지도. 오히려 품질도 일정하고. 그런데, 한겨레가 일본 기술 홍보를?
인체에 무해한지 유해한지는 안나왔네. 유전자조작 콩도 처음에는 식량난을 타개할 신기술이라 열광 했었지.
우메즈 카즈오 '14세'를 현실로 만들 셈인가보네 치킨 조지 박사가 현실로 나오겠어
그럼 소고기 가격이 떨어지나요?
우리나라가 개발한게 아니면 그림의 떡일 뿐이다.
기술의 발전은 엄청나네요
참 대단 일본
중하위층은 이런 배양육먹고 상위층만 도살한 신선육을 먹는 미래가 오고 있네
으윀. 역겹다.
기기괴괴 아이디어 하나 또 나오게될까두렵다. 저러다 인육조직도 만들어파는건 아닐지
아 징그러
왜 목숨걸고 개발하겠냐 실제 소 키우는데 들어가는 물의 양과 배설물의 co2 때문에 결국 환경오염 이슈 때문에 지금처럼 대량 사육은 힘들것이다
저시탕도 보기엔 이쁜데 맛은 없고 너무 딱딱해
제5원소라는 영화가 얼마나 미래를 내다 봤는지 생각나네요
저런걸먹고크는 우리아이들은 과연....?
난그래도 소닭개돼지 잡아먹을래
그냥 좀 무섭다...
좋든 싫든 인류가 생존하기 위해서는 반드시 해야하는 연구이고 좀 더 현실적으로보면 하루라도 더 빨리 결과가 나와야 한다는것. 인정하기 싫어도 지구는 점점 동식물이 살기 힘든 기후로 변해가고 재배하고 키울 수 있는 땅도 점점 줄어드는 현실, 우리 먹거리 중 가장먼저 줄여야 하는게 육식인걸 감안하면 이런 연구는 더욱 탄력을 받아 진행되어야 한다고 본다
먹는거 가지고 장난치면 먹는사람 알걸린다
좀덜먹는방법으로 가지 저건좀
오우~ 우웩~ 니네 많이 먹어라~ 난 그냥 고기 조금만 먹을란다.
중국산이 아니라서 궁금해짐 ㅋㅋㅋㅋ중국산은 뭔가 찝찝 ㅋㅋㅋ알몸김치 이후 다 더러워보여
왜 유전자 변형 옥수수 먼저 생각났지...소 키우는 것보다 싸겠고 동물보호단체 환영하

난 23일마지막날예약하고 다음날받았는데 ㅋㅋㅋ
플립2도 좋아 그거써
이상 삼노비 선동 쓰레기레기 광고
6일전에 받은 나는 뭐가되누??????
혹해서 사려거든 단점 다 감수할 수 있으면 사라 ㅋㅋㅋㅋㅋ 접히는 보급폰 쓰는 느낌임. 내구성 구려서 어이없게 어디 하나 망가지고 수리비도 오지게 비싼데 그래도 1은 무상수리도 잘 해주고 유상도 70% 보험처리 해주는데 3부터는 얄짤 없을 듯 ㅋㅋㅋㅋㅋㅋ 1 유저들은 대부분 안갈아탐. 본인들이 겪는 고질적 단점이 크게 개선되지 않았거든 ㅋㅋㅋㅋㅋㅋㅋ
제발 아이폰 사세요 성능은 아이폰입니다 삼성바이럴마케팅 지긋지긋해(저도삼성광고에낚여서 갤럭시쓰고있슴)
스마트폰 하나에 100에서 200만윈 사이 도대체제정신들이냐 펴고 접고 아주불편할듯 요즘스마트폰은 무겁고 화면이 너무크다 이접는폰은 너무 뚜겁다 예전 얇고 작은아이폰같은폰좀 만들어라 디자인에만 치중하는 스마트폰정말 가격 거품임 몇달만 지나도 100이하도떨어진다 신형스마트폰 사는사람들 바보들임 돈 낭비임5년지난 스마트폰아직도 쓰는 사람입니다단종된 엘지폰정말가볍고 얇고 아직도 이상없습니다 삼성은스마트폰 가격거품좀 빼라 폰하나에일 이백 제정신들이 아님
인기 절정이랰!! ㅋㅋㅋㅋ 싼슝~~~~
삼성전자 주가 폭등하겠네. ㅋㅋ
불법보조금 나한테 걸리기만 해봐라. 신고해서 포상받아야지!
사전예약하고 신랑 블랙 받음 크림 아직 감감 무소식이런식으로 9월 말까지 지연 될거면 사전예약 취소 하고 아이폰 바꿀까 생각중
일단 디자인 예쁘니 다른건 다 용서합니다 ㅎㅎ
제트플립3 사용후기 엄청약하다 개통3일만에 액정화면이 일자로펴지지않음 ~~완전조심조심 다뤄야 하는유리폰이에요~~비추에요~~후회하고 있는중입니다.
모두가 거짓 곧 알게될걸
아이폰 미만잡
잇섭이 쓰레기라고 평한 그 휴대폰 ㅋ.폰팔이들 동원 사전예약 물량 역대급이라고 하고서는 실제는 삼성 무선사업부에서 현금 대량 살포해서 만든 허수라는 점.근데 아무도 뭐라고 하지 않으며 온통 삼성 빨아주기하고 자빠졌지.얼마나 급했으면 완성도 안 된 UDC 

주가방어용 기사..어차피 이따구로 운영하면 망하는건 시간문재..
그래픽좋은 바다이야기
엔시 망하길 소원 합니다
게임이 게임이 아닌 사행성 도박으로 변질된지 오래인 국내 게임 산업. 외국에서 손가락질 받고있다.
저넘이 사기꾼 두목이냐???
내가볼땐 리니지w나오면 진짜 부도날지도 모른다ㅋㅋㅋ
그게 되겠냐구 ㅋㅋ 이미 사람들은 리니지BM에 질렸다니까? 이번 유일등급 못 봤어? 20억 써야되는거? 집 한 채 써야 변신 하나 얻어 ㅋㅋ 근데 웃긴건 그거 질러서 얻어도 약관상 소유권은 엔씨한테 있고 유저는 그냥 사용만 하는거라면서 ㅋㅋㅋ 아파트 하나를 변신 1개에 쓰라니 ㅋㅋㅋ
AAA급 게임하나 못내고 콘솔시장 진출도 못하면서 사행성 게임으로 돈만 빨아먹는 회사
뭐가 문제인지 전혀 파악못하고 있음 다음주도 나락 예상한다
이제 다들 알거임 다들ㅋ 주가방어용에 나와도 폭망이라는걸ㅡㅡㅋ 리니지했던사람은 다시는 엔씨게임 안합니다
기자 이름 메모
공룡? 곧 멸종된다. 돈에 환장한 사기 도박이 정당화되는 게임을 규제 안하는 이 나라 법도 고치자.
상식 밖의 게임회사 그리고 그 대표..
리니지 22년 했다 솔직히 2억 정도 현질 해서 정말 재미있게 놀았다. 그러나 최근 5년정도?? 과금을 따라 갈수가 없어 접었다 라인생활 하며 나름 잘나갔어도 과금을 버틸수 없어 접었다. 엔씨는 선을 넘어도 너무 넘었다 세상에서 사라져야 하는 기업 1위는 엔씨다 마른수건을 짜도 물이 나온다고...해도해도 너무한다. 엔씨는 이제 역사속으로 사라지길 소망한다
리니지w 도 사기이면, 사기든 말든 관심없고, 리니지w가 마지막 기회일듯, 더는 없다. 도깨비 봤나?! 택진?! 엔씨는 사라진다. 마지막 캐쉬 빨아먹고 잊혀지든 한번더 기회를 잡든 네 맘대로 하세요. 린저씨 올림.
그러기엔 당신도이미 너무늙고변해버렸다.탲진씨.초심으로돌아가길.사람이 마무리는아름다워야지.지금의엔씨는 너무 추하고더럽다
내가 기자였으면 도깨비 영상 보고나면 이런 기사 쓸 생각 1도 안나겠다. 무슨 엔씨 전속 기자도 아니고 돈이 NC만 있나

겁나게 우려먹네
그래서 언제 나온다냐? 국민이 호구로보이냐
위상이 있었어 ? ㅋㅋ
정말 기업이미지가 이정도로 추락하다니.
돈주고기사썼구나
Ea 보다 진성 끝판왕 세계에 그 악명 많이 펼치시길쪽팔린다....
리니지는 요즘 중징년층이나 노년층일부 나이좀 지극하신 주부들이외에는 안하드만젊은애들은 안허지
옆동네 펄어비스는 dokev
자체적으로 주가방어도 못하나보네 이런 찌라시만 뿌리고
24년간 집대성한 등골빼먹기
멀또 찾아와... 찾아오지말아줘 제발
이젠 전 세계적으로 망신 당할 차례야 ㅋㅋ
ㅋㅋ 과연 성공할것인가트릭스터,블소2?ㅋㅋㅋㅋㅋㅋㅋ
리니지 IP? 지나가던 개가 웃겠다 ㅋㅋㅋ 그냥 돈미새 그이상 그이하도 아님
안망했냐?
"유일" 다음은 "절대유일" 등급 낼걸? 이건 한 20억 꼴아박게 할려나? 리니지W 다음은 리니지 X,리니지Y, 리니지Z ... 도박장 수입이 짭짤하니 계속 호구들 절찬리 모집하겄지.
오로지 월정액만 하면 민심 좀 돌아 올거다
리니지m 동일한 운영체제에 확장성만으론 힘들어요 택진이형 메타로가지못하고 아날로그로가내
얘를 과학자상을 준거는 지금도 이해불가다,,,
task:  180
설레발 치지 마라, 성공하고 떠들어라.
대륙간 탄도미사일 도 같이 만들어 신속히 배치해서 중국 러시아 일본의 주요 타겟 에 맞추어 놓아라
해볼만한 산업 ... 수효 타당성도 잘 검증해보자...
Goooooo~d !!
이제우리도 좀 고부가 물건좀 팔자 3d업종에 대량으로 외노자 수입 필요없는 소량으로 비싼거좀 만들어팔자
꼭 성공해야 함!
우리 나라의 산업이 놀랍게 발달했군요. 저는 치아도금면봉을 개발하여 치석방지하는 물질을 판매하게 되어 위메프와 쿠팡에서 판매중입니다. 알로에나노입자포티스로 검색바랍니다.
비행기도 부픔이 20만개인데 이건 기자들이 쓴 내용입니다무슨 로켓이 37만개야부품 갯수나 알고 기사화 시키는것인지공부좀 하고 기사화 하세요
피망뉴맞고 넘무넘무 재밌습니다.
task:  181
ㅋㅋㅋ구냥 12쓰자 아이폰 어차피 맨날 똑같이 나오자나
삼성거 플립이 더이쁨
비

KeyboardInterrupt: 